### Full of Features

#### Libraries

In [1]:
from sklearn.model_selection import cross_val_score
import numpy as np
import pandas as pd
from collections import defaultdict
from sklearn.model_selection import KFold
from sklearn.metrics import mean_squared_error
from math import sqrt
from catboost import CatBoostRegressor, Pool
import pickle

pd.set_option('display.max_columns', 500)

#### Load Data

In [2]:
data_dir = '/Users/konstantinivanov/Documents/work/PIK/files-pik_digital_day_final'
input_dir = '/Users/konstantinivanov/Documents/work/PIK/input'
output_dir = '/Users/konstantinivanov/Documents/work/PIK/output'
sub_dir = '/Users/konstantinivanov/Documents/work/PIK/sub'

#### First Month - Matching start_square

Готовлю данные из февраля

In [3]:
train_data = pd.read_csv(data_dir + '/train.csv', encoding='cp1251')
test_data = pd.read_csv(data_dir + '/test.csv', encoding='cp1251')
#flat = pd.read_csv(wd + '/flat.csv', encoding='cp1251')
#price = pd.read_csv(wd + '/price.csv', encoding='cp1251')
#status = pd.read_csv(wd + '/status.csv', encoding='cp1251')

In [4]:
train_data.head()

id                               bulk_id  spalen       date1  start_square  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-10-01       13109.9   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2017-10-01       19898.4   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2017-10-01        2100.0   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2017-10-01        9614.9   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-11-01       11947.2   

    value          price  mean_sq  mean_fl  plan_s  plan_m  plan_l  vid_0  \
0  1124.5  135633.913043    38.00        8     147     198       0      0   
1  1412.3  128492.419825    58.01        9     139     120      83     30   
2   345.0  158237.634409    22.58       10      78      15       0      0   
3   769.4  123250.000000    78.81        8      50       0      72      0   
4   526.7  139420.634921    37.93        9     140     175       0      0   

   vid_1  vid_2  month  month_cnt Класс объекта  Количество помещений  \
0    169    176     10         34        эконом                  1983   
1    136    177     10         34        эконом                  1983   
2     73     20     10         34        эконом                  1983   
3     30     92     10         34        эконом                  1983   
4    145    170     11         35        эконом                  1983   

  Огорожена территория  Площадь земельного участка Входные группы  \
0                  нет                        17.0             да   
1                  нет                        17.0             да   
2                  нет                        17.0             да   
3                  нет                        17.0             да   
4                  нет                        17.0             да   

   Детский сад  Школа  Поликлиника  ФОК Спортивная площадка Автомойка  \
0          345    825            0    0                  да       нет   
1          345    825            0    0                  да       нет   
2          345    825            0    0                  да       нет   
3          345    825            0    0                  да       нет   
4          345    825            0    0                  да       нет   

  Кладовые Колясочные  Кондиционирование  Вентлияция  Лифт  \
0       да         да                  1           1     1   
1       да         да                  1           1     1   
2       да         да                  1           1     1   
3       да         да                  1           1     1   
4       да         да                  1           1     1   

  Система мусоротведения  Видеонаблюдение Подземная парковка Двор без машин  \
0             контейнеры                0                 да             да   
1             контейнеры                0                 да             да   
2             контейнеры                0                 да             да   
3             контейнеры                0                 да             да   
4             контейнеры                0                 да             да   

   Машиномест  Площадь пром. зоны в радиусе 500 м  \
0        1800                               65357   
1        1800                               65357   
2        1800                               65357   
3        1800                               65357   
4        1800                               65357   

   Площадь зеленой зоны в радиусе 500 м  До Кремля  До ТТК(км)  \
0                                 25533       18.0        12.0   
1                                 25533       18.0        12.0   
2                                 25533       18.0        12.0   
3                                 25533       18.0        12.0   
4                                 25533       18.0        12.0   

   До Садового(км)  До большой дороги на машине(км)  \
0             16.0                             0.55   
1             16.0                             0.55   
2             16.0             

In [5]:
test_data.head()

id                               bulk_id  spalen       date1  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   

           price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  147387.111111    37.99        9      3         39        эконом   
1  138465.811966    57.80        9      3         39        эконом   
2  171589.583333    23.67       10      3         39        эконом   
3  134381.707317    80.46        8      3         39        эконом   
4  153177.777778    38.00        9      4         40        эконом   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1983                  нет                        17.0   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Спортивная площадка  \
0             да          345    825            0    0                  да   
1             да          345    825            0    0                  да   
2             да          345    825            0    0                  да   
3             да          345    825            0    0                  да   
4             да          345    825            0    0                  да   

  Автомойка Кладовые Колясочные  Кондиционирование  Вентлияция  Лифт  \
0       нет       да         да                  1           1     1   
1       нет       да         да                  1           1     1   
2       нет       да         да                  1           1     1   
3       нет       да         да                  1           1     1   
4       нет       да         да                  1           1     1   

  Система мусоротведения  Видеонаблюдение Подземная парковка Двор без машин  \
0             контейнеры                0                 да             да   
1             контейнеры                0                 да             да   
2             контейнеры                0                 да             да   
3             контейнеры                0                 да             да   
4             контейнеры                0                 да             да   

   Машиномест  Площадь пром. зоны в радиусе 500 м  \
0        1800                               65357   
1        1800                               65357   
2        1800                               65357   
3        1800                               65357   
4        1800                               65357   

   Площадь зеленой зоны в радиусе 500 м  До Кремля  До ТТК(км)  \
0                                 25533       18.0        12.0   
1                                 25533       18.0        12.0   
2                                 25533       18.0        12.0   
3                                 25533       18.0        12.0   
4                                 25533       18.0        12.0   

   До Садового(км)  До большой дороги на машине(км)  \
0             16.0                             0.55   
1             16.0                             0.55   
2             16.0                             0.55   
3             16.0                             0.55   
4             16.0                             0.55   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                  1.4           0.28   
1                                    1.7                  1.4           0.28   
2                                    1.7                  

In [6]:
set(test_data.date1)

{'2018-03-01', '2018-04-01', '2018-05-01'}

In [7]:
start_square_02 = train_data[train_data['date1']=='2018-02-01'][['bulk_id', 'spalen', 'start_square', 'value']]
start_square_02['start_square_next'] = start_square_02['start_square'] - start_square_02['value']
start_square_02 = start_square_02.reset_index().drop(['index', 'start_square', 'value'], axis=1)

In [8]:
start_square_02.head()

bulk_id  spalen  start_square_next
0  FF3814A9-9F7D-E711-8530-00505688958B       1             8547.7
1  FF3814A9-9F7D-E711-8530-00505688958B       2            13471.7
2  FF3814A9-9F7D-E711-8530-00505688958B       0             1136.0
3  FF3814A9-9F7D-E711-8530-00505688958B       3             6598.0
4  7726CF5A-CC0A-E511-8098-001EC9D56418       3              187.2

Готовлю тестовые данные из марта

In [9]:
test_sub_03 = test_data[test_data['date1']=='2018-03-01']
test_sub_03 = pd.merge(test_sub_03, start_square_02, how='inner', on=['bulk_id', 'spalen'])
test_sub_03 = test_sub_03.rename(index=str, columns={"start_square_next": "start_square"})
test_sub_03['plan'] = test_sub_03['start_square']/test_sub_03['mean_sq']
test_sub_03['plan'] = test_sub_03['plan'].astype(int)

In [10]:
test_sub_03.head()

id                               bulk_id  spalen       date1  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01   
4  20  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-03-01   

           price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  147387.111111    37.99        9      3         39        эконом   
1  138465.811966    57.80        9      3         39        эконом   
2  171589.583333    23.67       10      3         39        эконом   
3  134381.707317    80.46        8      3         39        эконом   
4  182700.000000    93.60        3      3         39       комфорт   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1094                  нет                         6.8   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Спортивная площадка  \
0             да          345    825            0    0                  да   
1             да          345    825            0    0                  да   
2             да          345    825            0    0                  да   
3             да          345    825            0    0                  да   
4             да          150    550            0    1                  да   

  Автомойка Кладовые Колясочные  Кондиционирование  Вентлияция  Лифт  \
0       нет       да         да                  1           1     1   
1       нет       да         да                  1           1     1   
2       нет       да         да                  1           1     1   
3       нет       да         да                  1           1     1   
4       нет       да         да                  1           1     1   

  Система мусоротведения  Видеонаблюдение Подземная парковка Двор без машин  \
0             контейнеры                0                 да             да   
1             контейнеры                0                 да             да   
2             контейнеры                0                 да             да   
3             контейнеры                0                 да             да   
4             контейнеры                1                 да             да   

   Машиномест  Площадь пром. зоны в радиусе 500 м  \
0        1800                               65357   
1        1800                               65357   
2        1800                               65357   
3        1800                               65357   
4         871                                4740   

   Площадь зеленой зоны в радиусе 500 м  До Кремля  До ТТК(км)  \
0                                 25533       18.0        12.0   
1                                 25533       18.0        12.0   
2                                 25533       18.0        12.0   
3                                 25533       18.0        12.0   
4                                156205       13.0         8.0   

   До Садового(км)  До большой дороги на машине(км)  \
0             16.0                             0.55   
1             16.0                             0.55   
2             16.0                             0.55   
3             16.0                             0.55   
4             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1

Готовлю тренировочные данные

In [11]:
train_data['plan'] = train_data['plan_s'] + train_data['plan_m'] + train_data['plan_l']

In [12]:
train_data.drop(['plan_s', 'plan_m', 'plan_l', 'vid_0', 'vid_1', 'vid_2', 'Система мусоротведения', 'Лифт', 'Спортивная площадка'], axis=1, inplace=True)
train_data.to_csv(input_dir + "/train_full_lastfeb.csv", index=False)

test_sub_03['value'] = 0
test_sub_03.drop(['Система мусоротведения', 'Лифт', 'Спортивная площадка'], axis=1, inplace=True)
test_sub_03.to_csv(input_dir + "/test_full_mar_.csv", index=False, columns = train_data.columns)

In [13]:
train_data.head()

id                               bulk_id  spalen       date1  start_square  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-10-01       13109.9   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2017-10-01       19898.4   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2017-10-01        2100.0   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2017-10-01        9614.9   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-11-01       11947.2   

    value          price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  1124.5  135633.913043    38.00        8     10         34        эконом   
1  1412.3  128492.419825    58.01        9     10         34        эконом   
2   345.0  158237.634409    22.58       10     10         34        эконом   
3   769.4  123250.000000    78.81        8     10         34        эконом   
4   526.7  139420.634921    37.93        9     11         35        эконом   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1983                  нет                        17.0   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          345    825            0    0       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                0   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да        1800   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                               65357                                 25533   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       18.0        12.0             16.0                             0.55   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                  1.4           0.28   
1                                    1.7                  1.4           0.28   
2                                    1.7                  1.4           0.28   
3                                    1.7                  1.4           0.28   
4                                    1.7                  1.4           0.28   

   До парк

In [14]:
test_sub_03.head()

id                               bulk_id  spalen       date1  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01   
4  20  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-03-01   

           price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  147387.111111    37.99        9      3         39        эконом   
1  138465.811966    57.80        9      3         39        эконом   
2  171589.583333    23.67       10      3         39        эконом   
3  134381.707317    80.46        8      3         39        эконом   
4  182700.000000    93.60        3      3         39       комфорт   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1094                  нет                         6.8   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          150    550            0    1       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                1   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да         871   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                                4740                                156205   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       13.0         8.0             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1.40           0.28   
3                                    1.7                 1.40           0.28   
4                                    7.0                 0.35           0.45   

   До парка(км)  До парка пешком(км)  Станций метро от кольца  Площадь двора  \
0          0.58                 0.93                        8 

#### Validation

In [19]:
TEST_FILE = input_dir + '/test_full_mar_.csv' #add
CD_FILE = input_dir + '/train_full_feat.txt'

train_data = pd.read_csv(input_dir + "/train_full_lastfeb.csv")
test_data = pd.read_csv(TEST_FILE)

In [21]:
K = 10

kf = KFold(n_splits=K, random_state=42, shuffle=True)
kf.get_n_splits(range(len(train_data)))

print(kf)  

for i, (train_index, valid_index) in enumerate(kf.split(range(len(train_data)))):
    train = train_data.loc[train_index]
    valid = train_data.loc[valid_index]

    train.to_csv(input_dir + f"/train_{i}.csv",index=False)
    valid.to_csv(input_dir + f"/valid_{i}.csv",index=False)

KFold(n_splits=10, random_state=42, shuffle=True)


#### Fit and Predict

In [22]:
test_pool = Pool(TEST_FILE, column_description=CD_FILE, has_header=True, delimiter=",")

In [23]:
iterations = 5000
learning_rate = 0.05
depth = 8
random_seed = 42

Regressors = [
    CatBoostRegressor(iterations=iterations, learning_rate=learning_rate, depth=depth, random_seed=random_seed)
]

In [24]:
def FitOnKFolds(model):
    cum_y_test = np.zeros((len(test_data), 1))
    pred_y_train = np.zeros((len(train_data), 1))
    
    for i in range(K):
        TRAIN_FILE = input_dir + f'/train_{i}.csv'
        VAL_FILE = input_dir + f'/valid_{i}.csv'
        
        train_pool = Pool(TRAIN_FILE, column_description=CD_FILE, has_header=True, delimiter=",")
        val_pool = Pool(VAL_FILE, column_description=CD_FILE, has_header=True, delimiter=",")
        
        model.fit(train_pool, eval_set = val_pool)
        pickle.dump(model, open(input_dir + f'mod_full_feat_lastfeb_{i}.sav', 'wb'))
        
        pred = model.predict(test_pool)
        cum_y_test += pred.reshape((len(test_data),1))
        
        pred = model.predict(val_pool)
        df = pd.read_csv(VAL_FILE)
        pred_y_train[df.id] = pred.reshape((len(df),1))
        
    return (cum_y_test/K).clip(int(min(train_data.value)), int(max(train_data.value))).reshape(-1),\
        sqrt(mean_squared_error(list(train_data['value']), list(pred_y_train)))

In [25]:
00

In [26]:
%%time

vec_qual = []

for itr, model in enumerate(Regressors):
    y_test, qual = FitOnKFolds(model)
    vec_qual.append(qual)
    write_ans(f'sub_mar_ctb_itr={iterations}_lr={learning_rate}_depth={depth}_fld={K}_{itr}vers', y_test)

0:	learn: 435.5277802	test: 417.2752434	best: 417.2752434 (0)	total: 120ms	remaining: 9m 57s
1:	learn: 425.0338641	test: 406.1757629	best: 406.1757629 (1)	total: 175ms	remaining: 7m 18s
2:	learn: 414.9849903	test: 395.8890528	best: 395.8890528 (2)	total: 212ms	remaining: 5m 53s
3:	learn: 405.1007329	test: 385.6087469	best: 385.6087469 (3)	total: 260ms	remaining: 5m 25s
4:	learn: 396.3191760	test: 376.3531684	best: 376.3531684 (4)	total: 284ms	remaining: 4m 43s
5:	learn: 387.3045002	test: 367.6786048	best: 367.6786048 (5)	total: 339ms	remaining: 4m 41s
6:	learn: 379.9318820	test: 360.0140531	best: 360.0140531 (6)	total: 354ms	remaining: 4m 12s
7:	learn: 371.7763074	test: 351.5502932	best: 351.5502932 (7)	total: 398ms	remaining: 4m 8s
8:	learn: 364.3200527	test: 343.9493729	best: 343.9493729 (8)	total: 442ms	remaining: 4m 5s
9:	learn: 357.6867889	test: 337.0069131	best: 337.0069131 (9)	total: 494ms	remaining: 4m 6s
10:	learn: 351.4241026	test: 330.1940123	best: 330.1940123 (10)	total: 53

90:	learn: 234.1981257	test: 228.3592456	best: 228.3592456 (90)	total: 4.67s	remaining: 4m 12s
91:	learn: 233.6759139	test: 227.9857185	best: 227.9857185 (91)	total: 4.71s	remaining: 4m 11s
92:	learn: 233.6252244	test: 227.9581437	best: 227.9581437 (92)	total: 4.74s	remaining: 4m 10s
93:	learn: 232.8676784	test: 227.5443020	best: 227.5443020 (93)	total: 4.79s	remaining: 4m 9s
94:	learn: 232.2039344	test: 227.2873476	best: 227.2873476 (94)	total: 4.83s	remaining: 4m 9s
95:	learn: 231.5954534	test: 226.6980428	best: 226.6980428 (95)	total: 4.89s	remaining: 4m 9s
96:	learn: 231.1349103	test: 226.3559566	best: 226.3559566 (96)	total: 4.94s	remaining: 4m 9s
97:	learn: 231.1315920	test: 226.3589908	best: 226.3559566 (96)	total: 4.94s	remaining: 4m 7s
98:	learn: 230.7441613	test: 226.0422409	best: 226.0422409 (98)	total: 5s	remaining: 4m 7s
99:	learn: 229.9537562	test: 225.5116493	best: 225.5116493 (99)	total: 5.05s	remaining: 4m 7s
100:	learn: 229.4476302	test: 225.0109521	best: 225.0109521 

178:	learn: 204.3493106	test: 209.5604866	best: 209.5604866 (178)	total: 9.62s	remaining: 4m 19s
179:	learn: 204.1143134	test: 209.5139594	best: 209.5139594 (179)	total: 9.68s	remaining: 4m 19s
180:	learn: 203.8099673	test: 209.3387082	best: 209.3387082 (180)	total: 9.73s	remaining: 4m 19s
181:	learn: 203.4382710	test: 209.4059058	best: 209.3387082 (180)	total: 9.79s	remaining: 4m 19s
182:	learn: 203.1674598	test: 209.3315954	best: 209.3315954 (182)	total: 9.84s	remaining: 4m 18s
183:	learn: 202.8505517	test: 209.1490799	best: 209.1490799 (183)	total: 9.88s	remaining: 4m 18s
184:	learn: 202.3514503	test: 208.8873589	best: 208.8873589 (184)	total: 9.93s	remaining: 4m 18s
185:	learn: 202.0953238	test: 208.7812686	best: 208.7812686 (185)	total: 9.97s	remaining: 4m 18s
186:	learn: 201.8341401	test: 208.5633160	best: 208.5633160 (186)	total: 10s	remaining: 4m 18s
187:	learn: 201.5949991	test: 208.4822057	best: 208.4822057 (187)	total: 10.1s	remaining: 4m 17s
188:	learn: 201.5751227	test: 20

265:	learn: 185.7112211	test: 202.6977605	best: 202.6977605 (265)	total: 14.8s	remaining: 4m 23s
266:	learn: 185.5176423	test: 202.5347438	best: 202.5347438 (266)	total: 14.8s	remaining: 4m 22s
267:	learn: 185.2324258	test: 202.3443224	best: 202.3443224 (267)	total: 14.9s	remaining: 4m 22s
268:	learn: 185.1732025	test: 202.3290629	best: 202.3290629 (268)	total: 14.9s	remaining: 4m 22s
269:	learn: 184.9844435	test: 202.1706477	best: 202.1706477 (269)	total: 15s	remaining: 4m 22s
270:	learn: 184.7506567	test: 202.0459230	best: 202.0459230 (270)	total: 15s	remaining: 4m 22s
271:	learn: 184.5706384	test: 201.9768994	best: 201.9768994 (271)	total: 15.1s	remaining: 4m 21s
272:	learn: 184.3871745	test: 202.0176315	best: 201.9768994 (271)	total: 15.1s	remaining: 4m 21s
273:	learn: 184.3291400	test: 201.9749775	best: 201.9749775 (273)	total: 15.2s	remaining: 4m 21s
274:	learn: 184.0227979	test: 201.8592878	best: 201.8592878 (274)	total: 15.3s	remaining: 4m 22s
275:	learn: 183.8901966	test: 201.

350:	learn: 174.8284984	test: 197.7970256	best: 197.7970256 (350)	total: 19.1s	remaining: 4m 12s
351:	learn: 174.8189801	test: 197.7942476	best: 197.7942476 (351)	total: 19.1s	remaining: 4m 12s
352:	learn: 174.5070287	test: 197.7811251	best: 197.7811251 (352)	total: 19.2s	remaining: 4m 12s
353:	learn: 174.3891189	test: 197.6148629	best: 197.6148629 (353)	total: 19.2s	remaining: 4m 12s
354:	learn: 174.3226409	test: 197.6040544	best: 197.6040544 (354)	total: 19.3s	remaining: 4m 12s
355:	learn: 174.0240779	test: 197.3329773	best: 197.3329773 (355)	total: 19.3s	remaining: 4m 12s
356:	learn: 173.9716467	test: 197.3044763	best: 197.3044763 (356)	total: 19.4s	remaining: 4m 12s
357:	learn: 173.8132232	test: 197.3741896	best: 197.3044763 (356)	total: 19.4s	remaining: 4m 12s
358:	learn: 173.6616863	test: 197.2950851	best: 197.2950851 (358)	total: 19.5s	remaining: 4m 11s
359:	learn: 173.3647257	test: 197.1844607	best: 197.1844607 (359)	total: 19.5s	remaining: 4m 11s
360:	learn: 173.1597616	test: 

...

4599:	learn: 80.6599309	test: 185.3265994	best: 185.2780362 (4590)	total: 4m 11s	remaining: 21.8s
4600:	learn: 80.6594744	test: 185.3229137	best: 185.2780362 (4590)	total: 4m 11s	remaining: 21.8s
4601:	learn: 80.6585875	test: 185.3208791	best: 185.2780362 (4590)	total: 4m 11s	remaining: 21.7s
4602:	learn: 80.6382896	test: 185.3404719	best: 185.2780362 (4590)	total: 4m 11s	remaining: 21.7s
4603:	learn: 80.6293876	test: 185.3506776	best: 185.2780362 (4590)	total: 4m 11s	remaining: 21.6s
4604:	learn: 80.6159894	test: 185.3597348	best: 185.2780362 (4590)	total: 4m 11s	remaining: 21.6s
4605:	learn: 80.6135373	test: 185.3490348	best: 185.2780362 (4590)	total: 4m 11s	remaining: 21.5s
4606:	learn: 80.6093067	test: 185.3555950	best: 185.2780362 (4590)	total: 4m 11s	remaining: 21.4s
4607:	learn: 80.6044169	test: 185.3583713	best: 185.2780362 (4590)	total: 4m 11s	remaining: 21.4s
4608:	learn: 80.5849504	test: 185.3463720	best: 185.2780362 (4590)	total: 4m 11s	remaining: 21.3s
4609:	learn: 80.5803

4686:	learn: 80.0782239	test: 185.3032015	best: 185.2780362 (4590)	total: 4m 15s	remaining: 17.1s
4687:	learn: 80.0691758	test: 185.3076338	best: 185.2780362 (4590)	total: 4m 15s	remaining: 17s
4688:	learn: 80.0367820	test: 185.3012258	best: 185.2780362 (4590)	total: 4m 15s	remaining: 17s
4689:	learn: 80.0320960	test: 185.3007622	best: 185.2780362 (4590)	total: 4m 15s	remaining: 16.9s
4690:	learn: 80.0077950	test: 185.2704534	best: 185.2704534 (4690)	total: 4m 15s	remaining: 16.8s
4691:	learn: 80.0066341	test: 185.2740039	best: 185.2704534 (4690)	total: 4m 15s	remaining: 16.8s
4692:	learn: 80.0052482	test: 185.2676615	best: 185.2676615 (4692)	total: 4m 15s	remaining: 16.7s
4693:	learn: 79.9885907	test: 185.2761682	best: 185.2676615 (4692)	total: 4m 15s	remaining: 16.7s
4694:	learn: 79.9857285	test: 185.2777186	best: 185.2676615 (4692)	total: 4m 15s	remaining: 16.6s
4695:	learn: 79.9763592	test: 185.2731522	best: 185.2676615 (4692)	total: 4m 15s	remaining: 16.6s
4696:	learn: 79.9691185	

4773:	learn: 79.3840342	test: 185.1985467	best: 185.1712806 (4739)	total: 4m 20s	remaining: 12.3s
4774:	learn: 79.3835191	test: 185.2002803	best: 185.1712806 (4739)	total: 4m 20s	remaining: 12.3s
4775:	learn: 79.3773709	test: 185.2053797	best: 185.1712806 (4739)	total: 4m 20s	remaining: 12.2s
4776:	learn: 79.3671668	test: 185.1934415	best: 185.1712806 (4739)	total: 4m 20s	remaining: 12.2s
4777:	learn: 79.3644042	test: 185.1933068	best: 185.1712806 (4739)	total: 4m 20s	remaining: 12.1s
4778:	learn: 79.3640936	test: 185.1917402	best: 185.1712806 (4739)	total: 4m 20s	remaining: 12s
4779:	learn: 79.3539343	test: 185.1995259	best: 185.1712806 (4739)	total: 4m 20s	remaining: 12s
4780:	learn: 79.3421426	test: 185.1885249	best: 185.1712806 (4739)	total: 4m 20s	remaining: 11.9s
4781:	learn: 79.3377879	test: 185.1800940	best: 185.1712806 (4739)	total: 4m 20s	remaining: 11.9s
4782:	learn: 79.3327014	test: 185.1859843	best: 185.1712806 (4739)	total: 4m 20s	remaining: 11.8s
4783:	learn: 79.3247839	

4860:	learn: 78.7948487	test: 185.1780924	best: 185.1527696 (4827)	total: 4m 24s	remaining: 7.58s
4861:	learn: 78.7826091	test: 185.1941342	best: 185.1527696 (4827)	total: 4m 25s	remaining: 7.52s
4862:	learn: 78.7762811	test: 185.1761990	best: 185.1527696 (4827)	total: 4m 25s	remaining: 7.47s
4863:	learn: 78.7431780	test: 185.1746995	best: 185.1527696 (4827)	total: 4m 25s	remaining: 7.42s
4864:	learn: 78.7425899	test: 185.1761974	best: 185.1527696 (4827)	total: 4m 25s	remaining: 7.36s
4865:	learn: 78.7423455	test: 185.1741570	best: 185.1527696 (4827)	total: 4m 25s	remaining: 7.31s
4866:	learn: 78.7416433	test: 185.1754976	best: 185.1527696 (4827)	total: 4m 25s	remaining: 7.25s
4867:	learn: 78.7342390	test: 185.1726378	best: 185.1527696 (4827)	total: 4m 25s	remaining: 7.2s
4868:	learn: 78.7272330	test: 185.1749789	best: 185.1527696 (4827)	total: 4m 25s	remaining: 7.14s
4869:	learn: 78.7214143	test: 185.1796654	best: 185.1527696 (4827)	total: 4m 25s	remaining: 7.09s
4870:	learn: 78.71589

4945:	learn: 78.1233135	test: 185.1376879	best: 185.1019790 (4901)	total: 4m 30s	remaining: 2.95s
4946:	learn: 78.1095626	test: 185.1400823	best: 185.1019790 (4901)	total: 4m 30s	remaining: 2.9s
4947:	learn: 78.1064135	test: 185.1463719	best: 185.1019790 (4901)	total: 4m 30s	remaining: 2.84s
4948:	learn: 78.1042040	test: 185.1467744	best: 185.1019790 (4901)	total: 4m 30s	remaining: 2.79s
4949:	learn: 78.0804513	test: 185.1404770	best: 185.1019790 (4901)	total: 4m 30s	remaining: 2.73s
4950:	learn: 78.0756156	test: 185.1543051	best: 185.1019790 (4901)	total: 4m 30s	remaining: 2.68s
4951:	learn: 78.0744177	test: 185.1525351	best: 185.1019790 (4901)	total: 4m 30s	remaining: 2.62s
4952:	learn: 78.0651959	test: 185.1407779	best: 185.1019790 (4901)	total: 4m 30s	remaining: 2.57s
4953:	learn: 78.0540349	test: 185.1245569	best: 185.1019790 (4901)	total: 4m 30s	remaining: 2.52s
4954:	learn: 78.0523477	test: 185.1266049	best: 185.1019790 (4901)	total: 4m 30s	remaining: 2.46s
4955:	learn: 78.05205

In [ ]:
print(vec_qual)
#model = pickle.load(open(input_dir + f'mod_part_feat_{i}.sav', 'rb'))

In [27]:
y_test

array([8.11094601e+02, 1.25944387e+03, 1.88162684e+02, 6.45633283e+02,
       1.87585182e+01, 2.54373734e+02, 2.89414607e+02, 2.17975750e+02,
       3.55959822e+02, 3.46470991e+02, 5.29974450e+01, 4.81745132e+02,
       2.09402193e+01, 1.21336378e+02, 8.44906707e+01, 3.57669972e+02,
       1.12501530e+03, 3.30770002e+01, 2.50034467e+01, 1.42314889e+02,
       1.56357059e+02, 6.31172944e+02, 1.07757025e+02, 2.73395793e+02,
       3.64866183e+02, 1.67088656e+02, 2.73903208e+02, 3.39717351e+02,
       1.57970950e+02, 5.74300674e+02, 3.61303298e+01, 1.53865856e+02,
       2.61720221e+02, 2.02305947e+02, 1.42428089e+02, 0.00000000e+00,
       2.04919958e+02, 5.42722028e+02, 2.32212582e+02, 1.39027216e+02,
       3.93185223e+01, 3.17697914e+01, 4.37190971e+02, 2.87290816e+02,
       1.27067846e+02, 1.04293395e+03, 6.04582700e+02, 1.67182486e+03,
       4.96718897e+00, 3.48855793e+02, 1.00256621e+02, 2.72814935e+02,
       0.00000000e+00, 4.01857241e+02, 1.97480456e+02, 2.06753302e+02,
      

In [28]:
test_data_mar = test_data

In [29]:
test_data_mar['value'] = list(y_test)

In [30]:
test_data_mar

id                               bulk_id  spalen       date1  \
0       0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01   
1       1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01   
2       2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01   
3       3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01   
4      20  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-03-01   
5      23  72B1CAF6-A2DC-E511-9840-001EC9D56418       2  2018-03-01   
6      24  35168781-8F60-E611-9523-001EC9D5643C       3  2018-03-01   
7      25  35168781-8F60-E611-9523-001EC9D5643C       2  2018-03-01   
8      26  A8632090-8F60-E611-9523-001EC9D5643C       3  2018-03-01   
9      27  A8632090-8F60-E611-9523-001EC9D5643C       2  2018-03-01   
10     28  50B329EC-1DE2-E511-B953-001EC9D56418       3  2018-03-01   
11     29  F4BE45B2-AFF2-E611-84D2-001EC9D56418       3  2018-03-01   
12     30  F4BE45B2-AFF2-E611-84D2-001EC9D56418       1  2018-03-01   
13     31  F4BE45B2-AFF2-E611-84D2-001EC9D56418       4  2018-03-01   
14     32  F4BE45B2-AFF2-E611-84D2-001EC9D56418       2  2018-03-01   
15     33  832FDFD6-AFF2-E611-84D2-001EC9D56418       3  2018-03-01   
16     34  832FDFD6-AFF2-E611-84D2-001EC9D56418       2  2018-03-01   
17     36  A93667C6-B147-E311-8507-001EC9D5643C       2  2018-03-01   
18     37  E522EAD5-DA93-E311-8208-001EC9D56418       1  2018-03-01   
19     38  5C0E0157-C197-E711-8530-00505688958B       1  2018-03-01   
20     39  5C0E0157-C197-E711-8530-00505688958B       3  2018-03-01   
21     40  5C0E0157-C197-E711-8530-00505688958B       2  2018-03-01   
22     41  5C0E0157-C197-E711-8530-00505688958B       0  2018-03-01   
23     51  BC92BE33-C197-E711-8530-00505688958B       3  2018-03-01   
24     52  BC92BE33-C197-E711-8530-00505688958B       2  2018-03-01   
25     53  BC92BE33-C197-E711-8530-00505688958B       1  2018-03-01   
26     54  67127343-C197-E711-8530-00505688958B       3  2018-03-01   
27     55  67127343-C197-E711-8530-00505688958B       2  2018-03-01   
28     56  67127343-C197-E711-8530-00505688958B       1  2018-03-01   
29    123  BE6C758E-25F4-E611-84D2-001EC9D56418       2  2018-03-01   
..    ...                                   ...     ...         ...   
496  1707  51917AB1-4566-E711-97EC-001EC9D56418       2  2018-03-01   
497  1708  51917AB1-4566-E711-97EC-001EC9D56418       3  2018-03-01   
498  1709  9A2B12C5-4566-E711-97EC-001EC9D56418       3  2018-03-01   
499  1710  9A2B12C5-4566-E711-97EC-001EC9D56418       2  2018-03-01   
500  1711  9A2B12C5-4566-E711-97EC-001EC9D56418       1  2018-03-01   
501  1712  9A2B12C5-4566-E711-97EC-001EC9D56418       0  2018-03-01   
502  1713  9A2B12C5-4566-E711-97EC-001EC9D56418       4  2018-03-01   
503  1714  E51769DC-4566-E711-97EC-001EC9D56418       2  2018-03-01   
504  1715  E51769DC-4566-E711-97EC-001EC9D56418       1  2018-03-01   
505  1716  E51769DC-4566-E711-97EC-001EC9D56418       3  2018-03-01   
506  1717  E51769DC-4566-E711-97EC-001EC9D56418       4  2018-03-01   
507  1754  8CEB3310-63E8-E611-B887-001EC9D5643C       4  2018-03-01   
508  1755  8CEB3310-63E8-E611-B887-001EC9D5643C       2  2018-03-01   
509  1756  8CEB3310-63E8-E611-B887-001EC9D5643C       1  2018-03-01   
510  1757  8CEB3310-63E8-E611-B887-001EC9D5643C       3  2018-03-01   
511  1758  8CEB3310-63E8-E611-B887-001EC9D5643C       0  2018-03-01   
512  1759  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       1  2018-03-01   
513  1760  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       2  2018-03-01   
514  1761  C0B1362A-C378-E511-B4A4-001EC9D5643C       2  2018-03-01   
515  1762  C0B1362A-C378-E511-B4A4-001EC9D5643C       3  2018-03-01   
516  1763  C0B1362A-C378-E511-B4A4-001EC9D5643C       1  2018-03-01   
517  1764  999F708D-4FE9-E711-B9FF-00505688958B       0  2018-03-01   
518  1765  999F708D-4FE9-E711-B9FF-00505688958B       1  2018-03-01   
519  1766  999F708D-4FE9-E711-B9FF-00505688958B       2  2018-03-01   
520  1767  999F708D-4FE9-E711-B

#### Unload Data

In [31]:
test_data_mar.to_csv(sub_dir + f"/subsub_full_feat_mer.csv")